In [1]:
from ase_interface import ANIENS
from ase_interface import ensemblemolecule_multigpu
from ase_interface import ensemblemolecule

import pyNeuroChem as pync
import pyaniasetools as pya
import hdnntools as hdt

import numpy as np
import  ase

import time

import os
os.environ["OMP_NUM_THREADS"] = "8"

import  ase
from ase.md.langevin import Langevin
from ase.md.verlet import VelocityVerlet
from ase.io.trajectory import Trajectory
from ase import units

from ase.optimize.fire import FIRE as QuasiNewton
from ase.optimize import LBFGS

from ase.md.nvtberendsen import NVTBerendsen
from ase.md import MDLogger

from ase.io import read, write

from ase.parallel import world

In [2]:
dir = '/home/jsmith48/scratch/MD_TEST/malonaldehyde/'

fname = 'malonaldehyde'

# Molecule file
molfile = dir + fname + '.xyz'

# Dynamics file
xyzfile = dir + 'mdcrd2.xyz'

# Trajectory file
trajfile = dir + 'traj2.dat'

# Optimized structure out:
optfile = dir + 'opt_' +  fname +'2.xyz'

dt = 0.25
C = 0.0001 # Optimization convergence

ntdir = '/home/jsmith48/scratch/ccsd_extrapolation/final_train_models_3/ani-1x_tlcc_x8ens_2/'
cns = ntdir + 'rHCNO-5.2R_16-3.5A_a4-8.params'
sae = ntdir + 'sae_linfit.dat'
nnf = ntdir + 'train'
Nn = 8

In [3]:
#tvec = np.loadtxt('/home/jsmith48/scratch/carbon_nano_tube/new_test/'+fname+'.tvec',dtype=str)
#tvec = np.array(tvec[:,1:],dtype=np.float64)

In [4]:
#tvec

In [5]:
# Load molecule
mol = read(molfile)
# L = 40.0
# mol.set_cell(([[100.0, 0, 0],
#                [0, 35.0, 0],
#                [0, 0, 35.0]]))

#mol.set_cell((tvec))


#mol.set_pbc((True, True, True))
#mol.set_pbc((False, False, False))

# Set NC
aens = ensemblemolecule(cns, sae, nnf, Nn, 0)
#aens = ensemblemolecule(cns, sae, nnf, Nn, 1)

# Set ANI calculator
mol.set_calculator(ANIENS(aens))

s_time = time.time()
E = mol.get_potential_energy()
F = mol.get_forces()
print('Total time:',time.time()-s_time)

print(E)

spc = mol.get_chemical_symbols()
print(len(spc))

Total time: 0.04645252227783203
-7262.461488726974
9


In [6]:
# Optimize molecule
start_time = time.time()
dyn = LBFGS(mol)
dyn.run(fmax=C,steps=3000)
print('[ANI Total time:', time.time() - start_time, 'seconds]')

# Save optimized mol
spc = mol.get_chemical_symbols()
pos = mol.get_positions(wrap=False).reshape(1,len(spc),3)


hdt.writexyzfile(optfile, pos, spc)

       Step     Time          Energy         fmax
LBFGS:    0 10:11:05    -7262.461489        1.8032
LBFGS:    1 10:11:05    -7262.495287        1.1761
LBFGS:    2 10:11:05    -7262.509552        0.2954
LBFGS:    3 10:11:06    -7262.514261        0.2306
LBFGS:    4 10:11:06    -7262.518477        0.1644
LBFGS:    5 10:11:06    -7262.520572        0.2465
LBFGS:    6 10:11:06    -7262.522181        0.1260
LBFGS:    7 10:11:06    -7262.523746        0.0993
LBFGS:    8 10:11:06    -7262.524241        0.0728
LBFGS:    9 10:11:06    -7262.524432        0.0495
LBFGS:   10 10:11:06    -7262.524687        0.0530
LBFGS:   11 10:11:06    -7262.524912        0.0567
LBFGS:   12 10:11:06    -7262.525115        0.0596
LBFGS:   13 10:11:06    -7262.525251        0.0385
LBFGS:   14 10:11:06    -7262.525305        0.0196
LBFGS:   15 10:11:06    -7262.525325        0.0093
LBFGS:   16 10:11:06    -7262.525332        0.0099
LBFGS:   17 10:11:06    -7262.525341        0.0101
LBFGS:   18 10:11:06    -7262.52

In [7]:
# We want to run MD with constant energy using the VelocityVerlet algorithm.
#dyn = NVTBerendsen(mol, 1 * units.fs, 100.0, taut=1.0*1000*units.fs)
# coefficient to 0.04 atomic units.
dyn = Langevin(mol, dt * units.fs, 1.0 * units.kB, 0.04)

In [ ]:
# Open MD output
mdcrd = open(xyzfile,'w')

# Open MD output
traj = open(trajfile,'w')

# Define the printer
def storeenergy(a=mol, d=dyn, b=mdcrd, t=traj):  # store a reference to atoms in the definition.
    """Function to print the potential, kinetic and total energy."""
    epot = a.get_potential_energy() / len(a)
    ekin = a.get_kinetic_energy() / len(a)

    stddev =  hdt.evtokcal*a.calc.stddev
    Fstddev =  hdt.evtokcal*a.calc.Fstddev

    t.write(str(d.get_number_of_steps()) + ' ' + str(ekin / (1.5 * units.kB)) + ' ' + str(epot) + ' ' + str(ekin) + ' ' + str(epot+ekin) + ' ' + str(stddev) + '\n')
    b.write(str(len(a)) + '\n' + str(ekin / (1.5 * units.kB)) + ' Step: ' + str(d.get_number_of_steps()) + '\n')
    c = a.get_positions(wrap=False)
    for j, i in zip(a, c):
        b.write(str(j.symbol) + ' ' + str(i[0]) + ' ' + str(i[1]) + ' ' + str(i[2]) + '\n')

    print('Step: %d Energy per atom: Epot = %.3f  Ekin = %.3f (T=%.3fK)  '
          'Etot = %.6f Esig = %.3f Fsig = %.3f' % (d.get_number_of_steps(), epot, ekin, ekin / (1.5 * units.kB), epot + ekin, stddev,Fstddev))
    
# Set the printer
dyn.attach(storeenergy, interval=50)

In [ ]:
start_time = time.time()
dyn.set_temperature(300. * units.kB)
dyn.run(40000000)
print('[ANI Total time:', time.time() - start_time, 'seconds]')

Step: 50 Energy per atom: Epot = -806.945  Ekin = 0.001 (T=7.802K)  Etot = -806.944158 Esig = 0.353 Fsig = 0.132
Step: 100 Energy per atom: Epot = -806.945  Ekin = 0.003 (T=23.895K)  Etot = -806.941792 Esig = 0.362 Fsig = 0.126
Step: 150 Energy per atom: Epot = -806.943  Ekin = 0.005 (T=36.097K)  Etot = -806.938192 Esig = 0.354 Fsig = 0.132
Step: 200 Energy per atom: Epot = -806.943  Ekin = 0.007 (T=56.045K)  Etot = -806.935863 Esig = 0.406 Fsig = 0.131
Step: 250 Energy per atom: Epot = -806.939  Ekin = 0.007 (T=54.574K)  Etot = -806.931845 Esig = 0.284 Fsig = 0.125
Step: 300 Energy per atom: Epot = -806.941  Ekin = 0.012 (T=94.493K)  Etot = -806.928694 Esig = 0.403 Fsig = 0.128
Step: 350 Energy per atom: Epot = -806.937  Ekin = 0.010 (T=80.336K)  Etot = -806.926791 Esig = 0.311 Fsig = 0.129
Step: 400 Energy per atom: Epot = -806.939  Ekin = 0.017 (T=132.098K)  Etot = -806.922249 Esig = 0.314 Fsig = 0.115
Step: 450 Energy per atom: Epot = -806.932  Ekin = 0.014 (T=104.669K)  Etot = -80

Step: 3550 Energy per atom: Epot = -806.913  Ekin = 0.037 (T=287.604K)  Etot = -806.876168 Esig = 0.285 Fsig = 0.141
Step: 3600 Energy per atom: Epot = -806.917  Ekin = 0.045 (T=345.298K)  Etot = -806.872260 Esig = 0.372 Fsig = 0.119
Step: 3650 Energy per atom: Epot = -806.923  Ekin = 0.055 (T=422.532K)  Etot = -806.868513 Esig = 0.214 Fsig = 0.150
Step: 3700 Energy per atom: Epot = -806.907  Ekin = 0.046 (T=356.627K)  Etot = -806.861017 Esig = 0.474 Fsig = 0.168
Step: 3750 Energy per atom: Epot = -806.914  Ekin = 0.044 (T=341.228K)  Etot = -806.870013 Esig = 0.380 Fsig = 0.137
Step: 3800 Energy per atom: Epot = -806.906  Ekin = 0.036 (T=281.637K)  Etot = -806.869202 Esig = 0.407 Fsig = 0.140
Step: 3850 Energy per atom: Epot = -806.921  Ekin = 0.057 (T=438.861K)  Etot = -806.864296 Esig = 0.463 Fsig = 0.157
Step: 3900 Energy per atom: Epot = -806.912  Ekin = 0.039 (T=301.711K)  Etot = -806.872783 Esig = 0.297 Fsig = 0.157
Step: 3950 Energy per atom: Epot = -806.909  Ekin = 0.039 (T=303

Step: 7100 Energy per atom: Epot = -806.924  Ekin = 0.025 (T=193.375K)  Etot = -806.899364 Esig = 0.408 Fsig = 0.154
Step: 7150 Energy per atom: Epot = -806.922  Ekin = 0.023 (T=178.097K)  Etot = -806.899196 Esig = 0.341 Fsig = 0.134
Step: 7200 Energy per atom: Epot = -806.926  Ekin = 0.020 (T=155.104K)  Etot = -806.905464 Esig = 0.414 Fsig = 0.152
Step: 7250 Energy per atom: Epot = -806.928  Ekin = 0.017 (T=134.208K)  Etot = -806.910243 Esig = 0.403 Fsig = 0.151
Step: 7300 Energy per atom: Epot = -806.933  Ekin = 0.025 (T=194.998K)  Etot = -806.907640 Esig = 0.254 Fsig = 0.134
Step: 7350 Energy per atom: Epot = -806.927  Ekin = 0.016 (T=126.868K)  Etot = -806.910255 Esig = 0.469 Fsig = 0.135
Step: 7400 Energy per atom: Epot = -806.921  Ekin = 0.018 (T=138.624K)  Etot = -806.903344 Esig = 0.298 Fsig = 0.131
Step: 7450 Energy per atom: Epot = -806.927  Ekin = 0.023 (T=175.472K)  Etot = -806.904131 Esig = 0.271 Fsig = 0.135
Step: 7500 Energy per atom: Epot = -806.935  Ekin = 0.026 (T=203

Step: 10600 Energy per atom: Epot = -806.914  Ekin = 0.036 (T=276.533K)  Etot = -806.878058 Esig = 0.389 Fsig = 0.137
Step: 10650 Energy per atom: Epot = -806.927  Ekin = 0.042 (T=325.756K)  Etot = -806.885121 Esig = 0.308 Fsig = 0.159
Step: 10700 Energy per atom: Epot = -806.923  Ekin = 0.043 (T=331.956K)  Etot = -806.879758 Esig = 0.319 Fsig = 0.141
Step: 10750 Energy per atom: Epot = -806.909  Ekin = 0.034 (T=263.074K)  Etot = -806.874819 Esig = 0.273 Fsig = 0.146
Step: 10800 Energy per atom: Epot = -806.902  Ekin = 0.031 (T=237.792K)  Etot = -806.871262 Esig = 0.285 Fsig = 0.141
Step: 10850 Energy per atom: Epot = -806.906  Ekin = 0.036 (T=279.222K)  Etot = -806.869656 Esig = 0.310 Fsig = 0.142
Step: 10900 Energy per atom: Epot = -806.907  Ekin = 0.043 (T=331.308K)  Etot = -806.864052 Esig = 0.282 Fsig = 0.143
Step: 10950 Energy per atom: Epot = -806.918  Ekin = 0.054 (T=420.294K)  Etot = -806.863964 Esig = 0.344 Fsig = 0.147
Step: 11000 Energy per atom: Epot = -806.907  Ekin = 0.0

Step: 14100 Energy per atom: Epot = -806.923  Ekin = 0.044 (T=343.801K)  Etot = -806.878846 Esig = 0.376 Fsig = 0.150
Step: 14150 Energy per atom: Epot = -806.911  Ekin = 0.034 (T=265.578K)  Etot = -806.876723 Esig = 0.429 Fsig = 0.141
Step: 14200 Energy per atom: Epot = -806.916  Ekin = 0.038 (T=292.303K)  Etot = -806.878143 Esig = 0.385 Fsig = 0.161
Step: 14250 Energy per atom: Epot = -806.922  Ekin = 0.033 (T=252.958K)  Etot = -806.888831 Esig = 0.302 Fsig = 0.156
Step: 14300 Energy per atom: Epot = -806.909  Ekin = 0.018 (T=139.493K)  Etot = -806.890691 Esig = 0.327 Fsig = 0.145
Step: 14350 Energy per atom: Epot = -806.916  Ekin = 0.027 (T=208.221K)  Etot = -806.888738 Esig = 0.311 Fsig = 0.131
Step: 14400 Energy per atom: Epot = -806.920  Ekin = 0.035 (T=270.725K)  Etot = -806.885413 Esig = 0.246 Fsig = 0.135
Step: 14450 Energy per atom: Epot = -806.927  Ekin = 0.036 (T=276.659K)  Etot = -806.891309 Esig = 0.323 Fsig = 0.129
Step: 14500 Energy per atom: Epot = -806.920  Ekin = 0.0

...

Step: 1584050 Energy per atom: Epot = -806.927  Ekin = 0.052 (T=404.232K)  Etot = -806.874434 Esig = 0.356 Fsig = 0.145
Step: 1584100 Energy per atom: Epot = -806.918  Ekin = 0.042 (T=326.992K)  Etot = -806.875420 Esig = 0.442 Fsig = 0.141
Step: 1584150 Energy per atom: Epot = -806.916  Ekin = 0.036 (T=276.883K)  Etot = -806.879779 Esig = 0.378 Fsig = 0.142
Step: 1584200 Energy per atom: Epot = -806.920  Ekin = 0.035 (T=267.701K)  Etot = -806.885209 Esig = 0.319 Fsig = 0.138
Step: 1584250 Energy per atom: Epot = -806.927  Ekin = 0.044 (T=337.273K)  Etot = -806.883343 Esig = 0.305 Fsig = 0.161
Step: 1584300 Energy per atom: Epot = -806.929  Ekin = 0.045 (T=345.970K)  Etot = -806.883895 Esig = 0.336 Fsig = 0.146
Step: 1584350 Energy per atom: Epot = -806.912  Ekin = 0.035 (T=269.255K)  Etot = -806.877446 Esig = 0.348 Fsig = 0.152
Step: 1584400 Energy per atom: Epot = -806.926  Ekin = 0.043 (T=336.048K)  Etot = -806.882199 Esig = 0.386 Fsig = 0.150
Step: 1584450 Energy per atom: Epot = -8

Step: 1587500 Energy per atom: Epot = -806.896  Ekin = 0.036 (T=275.048K)  Etot = -806.860568 Esig = 0.271 Fsig = 0.145
Step: 1587550 Energy per atom: Epot = -806.899  Ekin = 0.038 (T=290.739K)  Etot = -806.861149 Esig = 0.320 Fsig = 0.142
Step: 1587600 Energy per atom: Epot = -806.900  Ekin = 0.037 (T=289.382K)  Etot = -806.862975 Esig = 0.328 Fsig = 0.131
Step: 1587650 Energy per atom: Epot = -806.915  Ekin = 0.058 (T=451.662K)  Etot = -806.856570 Esig = 0.347 Fsig = 0.151
Step: 1587700 Energy per atom: Epot = -806.902  Ekin = 0.047 (T=360.005K)  Etot = -806.855644 Esig = 0.508 Fsig = 0.155
Step: 1587750 Energy per atom: Epot = -806.919  Ekin = 0.062 (T=482.508K)  Etot = -806.856766 Esig = 0.297 Fsig = 0.172
Step: 1587800 Energy per atom: Epot = -806.915  Ekin = 0.051 (T=393.713K)  Etot = -806.864477 Esig = 0.403 Fsig = 0.149
Step: 1587850 Energy per atom: Epot = -806.902  Ekin = 0.032 (T=247.528K)  Etot = -806.869932 Esig = 0.412 Fsig = 0.144
Step: 1587900 Energy per atom: Epot = -8

Step: 1591000 Energy per atom: Epot = -806.929  Ekin = 0.036 (T=277.411K)  Etot = -806.893248 Esig = 0.444 Fsig = 0.129
Step: 1591050 Energy per atom: Epot = -806.913  Ekin = 0.022 (T=171.126K)  Etot = -806.890693 Esig = 0.290 Fsig = 0.157
Step: 1591100 Energy per atom: Epot = -806.930  Ekin = 0.040 (T=306.163K)  Etot = -806.890890 Esig = 0.353 Fsig = 0.135
Step: 1591150 Energy per atom: Epot = -806.911  Ekin = 0.019 (T=148.826K)  Etot = -806.891851 Esig = 0.447 Fsig = 0.134
Step: 1591200 Energy per atom: Epot = -806.926  Ekin = 0.036 (T=274.820K)  Etot = -806.890059 Esig = 0.279 Fsig = 0.145
Step: 1591250 Energy per atom: Epot = -806.919  Ekin = 0.027 (T=211.257K)  Etot = -806.891852 Esig = 0.306 Fsig = 0.132
Step: 1591300 Energy per atom: Epot = -806.922  Ekin = 0.030 (T=234.473K)  Etot = -806.891668 Esig = 0.295 Fsig = 0.136
Step: 1591350 Energy per atom: Epot = -806.915  Ekin = 0.020 (T=158.139K)  Etot = -806.894510 Esig = 0.230 Fsig = 0.134
Step: 1591400 Energy per atom: Epot = -8

Step: 1594450 Energy per atom: Epot = -806.928  Ekin = 0.031 (T=238.488K)  Etot = -806.897098 Esig = 0.353 Fsig = 0.150
Step: 1594500 Energy per atom: Epot = -806.922  Ekin = 0.024 (T=186.095K)  Etot = -806.897677 Esig = 0.400 Fsig = 0.150
Step: 1594550 Energy per atom: Epot = -806.928  Ekin = 0.030 (T=230.814K)  Etot = -806.897684 Esig = 0.263 Fsig = 0.148
Step: 1594600 Energy per atom: Epot = -806.926  Ekin = 0.028 (T=217.228K)  Etot = -806.897765 Esig = 0.486 Fsig = 0.144
Step: 1594650 Energy per atom: Epot = -806.920  Ekin = 0.020 (T=153.810K)  Etot = -806.900600 Esig = 0.309 Fsig = 0.136
Step: 1594700 Energy per atom: Epot = -806.927  Ekin = 0.031 (T=238.484K)  Etot = -806.896208 Esig = 0.401 Fsig = 0.141
Step: 1594750 Energy per atom: Epot = -806.920  Ekin = 0.032 (T=248.742K)  Etot = -806.887926 Esig = 0.222 Fsig = 0.135
Step: 1594800 Energy per atom: Epot = -806.918  Ekin = 0.023 (T=174.746K)  Etot = -806.895906 Esig = 0.297 Fsig = 0.124
Step: 1594850 Energy per atom: Epot = -8

Step: 1597950 Energy per atom: Epot = -806.926  Ekin = 0.029 (T=221.996K)  Etot = -806.897649 Esig = 0.340 Fsig = 0.164
Step: 1598000 Energy per atom: Epot = -806.928  Ekin = 0.039 (T=303.862K)  Etot = -806.888666 Esig = 0.326 Fsig = 0.142
Step: 1598050 Energy per atom: Epot = -806.921  Ekin = 0.030 (T=235.261K)  Etot = -806.891004 Esig = 0.311 Fsig = 0.148
Step: 1598100 Energy per atom: Epot = -806.912  Ekin = 0.020 (T=153.539K)  Etot = -806.892148 Esig = 0.585 Fsig = 0.172
Step: 1598150 Energy per atom: Epot = -806.927  Ekin = 0.033 (T=257.005K)  Etot = -806.894077 Esig = 0.330 Fsig = 0.140
Step: 1598200 Energy per atom: Epot = -806.923  Ekin = 0.029 (T=225.958K)  Etot = -806.893737 Esig = 0.396 Fsig = 0.147
Step: 1598250 Energy per atom: Epot = -806.921  Ekin = 0.025 (T=195.041K)  Etot = -806.895298 Esig = 0.404 Fsig = 0.160
Step: 1598300 Energy per atom: Epot = -806.929  Ekin = 0.034 (T=264.434K)  Etot = -806.895113 Esig = 0.298 Fsig = 0.156
Step: 1598350 Energy per atom: Epot = -8